In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

import numpy as np
import time

torch.manual_seed(1)

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

EMBED_SIZE = 256
HIDDEN_SIZE = 256

d = HIDDEN_SIZE

class BIDAF(nn.Module):
    def __init__(self):
        super().__init__()

        # layer 3: contextual embedding layer
        self.d = HIDDEN_SIZE
        self.layer3_context_lstm = nn.LSTM(EMBED_SIZE, self.d, bidirectional=True)
        self.layer3_context_hidden = self.init_hidden()
        self.layer3_query_lstm = nn.LSTM(EMBED_SIZE, self.d, bidirectional=True)
        self.layer3_query_hidden = self.init_hidden()

        # layer 4: attention flow layer
        self.layer4_w_s = nn.Linear(self.d*6, 1)

        # layer 5: modeling layer
        self.modeling_layer_lstm = nn.LSTM(self.d*8, self.d, num_layers=2, bidirectional=True)
        
        # layer 6: output layer
        self.output_layer_w_p1 = nn.Linear(self.d*10, 1)
        self.output_layer_w_p2 = nn.Linear(self.d*10, 1)
        self.output_layer_lstm = nn.LSTM(self.d*2, self.d, bidirectional=True)

    def init_hidden(self, dim0=1):
        return (torch.zeros(dim0, 1, self.d, device=device), torch.zeros(dim0, 1, self.d, device=device))

    # h size: 2d
    # U size: 2d * J
    # return size: 1 * J
    def alpha(self, h, U):
        J = U.size(1)
        h = h.unsqueeze(0)
        H_matrix = [h] * J
        H_matrix = torch.cat(H_matrix, dim=0)
        #print(H_matrix)
        #print(U.t())
        #print(h*U.t())

        # size: J * 6d
        concated_matrix = torch.cat([H_matrix, U.t(), h*U.t()], dim=1)
        #print(concated_matrix)

        # out size: J * 1
        out = self.layer4_w_s(concated_matrix)
        #print(out.t())

        return out.t()

    # input size: S * EMBED_SIZE
    def forward(self, context_word_vec, query_word_vec):
        T = context_word_vec.size(0)
        J = query_word_vec.size(0)
        
        context_wv = context_word_vec.view(T, 1, -1)
        #print(context_wv)

        out, hidden = self.layer3_context_lstm(context_wv, self.init_hidden(2))
        #print('out:\n', out)
        #print('hidden:\n', self.layer3_context_hidden)

        # H size: 2d * T
        H = out.view(T, -1).t()
        #print('H:\n', H)

        
        context_wv = query_word_vec.view(J, 1, -1)
        #print(context_wv)

        out, hidden = self.layer3_query_lstm(context_wv, self.init_hidden(2))
        #print('out:\n', out)

        # U size: 2d * J
        U = out.view(J, -1).t()
        #print('U:\n', U)


        # calculating similarity matrix 'S'
        #for t in len(T):
        #self.alpha(H[:, 0], U)
        S_rows = [self.alpha(H[:, t], U) for t in range(T)]
        S = torch.cat(S_rows, dim=0)
        #print('S:\n', S)

        # 计算Context_to_query Attention, size: 2d * T 
        S_softmaxed = F.softmax(S, dim=1)
        UU = torch.mm(S_softmaxed, U.t()).t()
        #print('UU:\n', UU)

        # 计算Query_to_context Attention
        b, _ = torch.max(S, dim=1, keepdim=True)
        b = F.softmax(b, dim=0)
        hh = torch.mm(H, b)
        HH = torch.cat([hh]*T, dim=1)

        G = torch.cat([H, UU, H*UU, H*HH], dim=0)
        #print(G)
        #print(G.size())


        ## 计算Modeling Layer
        M, hidden = self.modeling_layer_lstm(G.t().view(T, 1, -1), self.init_hidden(4))


        ## 计算Output Layer
        # 计算答案的起始位置概率分布
        out_matrix = torch.cat([G, M.view(T, -1).t()], dim=0)
        #print(out_matrix)
        p1 = self.output_layer_w_p1(out_matrix.t())
        p1 = p1.t()
        #print(p1)
        p1_proba = F.log_softmax(p1, dim=1)
        #print(p1_proba)

        # 计算答案的结束位置概率分布
        M2, hidden = self.output_layer_lstm(M, self.init_hidden(2))
        out_matrix = torch.cat([G, M2.view(T, -1).t()], dim=0)
        p2 = self.output_layer_w_p2(out_matrix.t())
        p2 = p2.t()
        #print(p2)
        p2_proba = F.log_softmax(p2, dim=1)
        #print(p2_proba)

        out = torch.cat([p1_proba, p2_proba], dim=0)
        #print(out)
        return out

cpu


In [3]:
## train
model = BIDAF()

if torch.cuda.is_available():
    model.cuda()
print(model)

loss_function = nn.NLLLoss()
#optimizer = optim.RMSprop(model.parameters())

BIDAF(
  (layer3_context_lstm): LSTM(256, 256, bidirectional=True)
  (layer3_query_lstm): LSTM(256, 256, bidirectional=True)
  (layer4_w_s): Linear(in_features=1536, out_features=1, bias=True)
  (modeling_layer_lstm): LSTM(2048, 256, num_layers=2, bidirectional=True)
  (output_layer_w_p1): Linear(in_features=2560, out_features=1, bias=True)
  (output_layer_w_p2): Linear(in_features=2560, out_features=1, bias=True)
  (output_layer_lstm): LSTM(512, 256, bidirectional=True)
)


In [4]:
import webqa

PATH = 'models/webqa_model/webqa_model_2018-10-11-18_2_59.sav'
model.load_state_dict(torch.load(PATH, map_location=device))
model.eval()

BIDAF(
  (layer3_context_lstm): LSTM(256, 256, bidirectional=True)
  (layer3_query_lstm): LSTM(256, 256, bidirectional=True)
  (layer4_w_s): Linear(in_features=1536, out_features=1, bias=True)
  (modeling_layer_lstm): LSTM(2048, 256, num_layers=2, bidirectional=True)
  (output_layer_w_p1): Linear(in_features=2560, out_features=1, bias=True)
  (output_layer_w_p2): Linear(in_features=2560, out_features=1, bias=True)
  (output_layer_lstm): LSTM(512, 256, bidirectional=True)
)

In [5]:
from rouge import Rouge

rouge = Rouge()

def best_match(start_prob, end_prob):
    best_indexes = (-1, -1)
    best_score = 1000000
    
    for end_idx, p2 in enumerate(end_prob):
        #print(end_idx, p2)
        p1, start_idx = torch.max(start_prob[:end_idx+1], dim=0)
        #print(p1, start_idx)
        
        score = p1*p2
        if score < best_score:
            best_score = score
            best_indexes = (start_idx.item(), end_idx)
            
            #print(score, p1, p2, start_idx, end_idx)
    
    return best_indexes

with torch.no_grad():
    matched = 0
    total = 0
    total_score = 0
    for query, context, target, qq, aa, cc in webqa.load_qa():
        query_in = query.view(query.size(0), 1, -1)
        context_in = context.view(context.size(0), 1, -1)

        out = model(context_in, query_in)
                
        total += 1
        predict = best_match(out[0], out[1])
        target = (target[0].item(), target[1].item())
        
        print()
        print('*'*50)
        doc = cc[:target[0]] + ['['] + cc[target[0]:target[1]+1] + [']'] + cc[target[1]+1:]
        print(''.join(doc))
        print('*question:', ''.join(qq))
        guess = cc[predict[0]:predict[1]+1]
        print('*predict:', ''.join(guess))
        
        if predict == target:
            matched += 1
            print('!! match !!')
        else:
            delta = out[0][predict[0]]*out[1][predict[1]] - out[0][target[0]]*out[1][target[1]]
            print('-- abs --:', torch.abs(delta).item())

        print('predict-target: {}-{}'.format(predict, target))
        try:
            scores = rouge.get_scores(' '.join(guess), ' '.join(aa))
            score_l = scores[0]['rouge-l']['f']
        except ValueError:
            score_l = 0
            
        if score_l > 0.999999:
            score_l = 1.0
        print('Rouge-L:', score_l)
        total_score += score_l
        
        #break
        
    print('matched/total:', matched/total)
    print('avg rouge-L score:', total_score/total)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache


total answers: 140897


Loading model cost 0.658 seconds.
Prefix dict has been built succesfully.



**************************************************
北宋末年(公元11,12世纪)出现的印刷报纸,不仅是[中国]新闻史上最早的印刷报纸,也是世界新闻史上最早的印刷报纸.中国新闻事业历史的悠久,内容的丰富,是任何西方国家都难以比肩的.<e>中国古代的报纸产生于中国的封建社会时期,是封建地主阶级及其政治代表占统治地位的封建自然经济通过新闻手段的反映.在漫长的封建社会时期,中国古代的报纸,不论是官方的邸报,还是民办的小报和京报,都必然要和当时的封建统治者保持一定的联系,受他们的制约.官方的邸报固然是封建统治阶级的喉舌和御用的宣传工具,民办的小报和京报也只能在封建统治阶级的控制下活动,不能越雷池一步.封建统治者绝不允许可以自由报道一切消息和自由发表一切意见的报纸存在.中国古代的报纸在为当时的读者提供朝野政治和社会信息方面确实起过一定的作用,但始终没有摆脱统治阶级的掌握.中国古代报纸的历史,基本上是一部封建统治阶级掌握传播媒介,控制舆论工具,限制言论出版自由的历史.<e>中国古代的邸报有1200年左右的历史.小报有近千年的历史.民间报房出版的邸报,京报有近400年的历史.它们从诞生到结束,持续的时间都不算短,但发展不快,形式内容的变化不大.
*question: 世界上最早的报纸诞生于
*predict: 中国
-- abs --: 7.384554386138916
predict-target: (34, 34)-(16, 16)
Rouge-L: 1.0

**************************************************
报纸从诞生到今天已经走过了漫长的历史，公元前60年，古罗马政治家恺撒把罗马市以及国家发生的时间书写在白色的木板上，告示市民。这便是世界上最古老的报纸。[中国]在7世纪，唐朝宫廷内就发行过手写的传阅版，这应该算是中国最早的报纸。
*question: 世界上最早的报纸诞生于
*predict: 中国在7世纪，唐朝
-- abs --: 0.5649175643920898
predict-target: (45, 50)-(45, 45)
Rouge-L: 0.17050691244221888

***********************************


**************************************************
由公鸡精子进入母鸡[体内]。体内受精，体外发育
*question: 鸡是怎么受精的
*predict: 体内
!! match !!
predict-target: (5, 5)-(5, 5)
Rouge-L: 1.0

**************************************************
送鸡毛信的抗日小英雄：[海娃]
*question: 鸡毛信的小英雄是谁
*predict: 海娃
!! match !!
predict-target: (7, 7)-(7, 7)
Rouge-L: 1.0

**************************************************
送鸡毛信的抗日小英雄——[海娃]12岁的儿童团团长海娃,他的任务是一边放羊,一边放哨,发现敌人,给村里人打信号。
*question: 鸡毛信的小英雄是谁
*predict: 海娃
!! match !!
predict-target: (8, 8)-(8, 8)
Rouge-L: 1.0

**************************************************
鸡毛信<e>的抗日小英雄——[海娃]
*question: 鸡毛信的小英雄是谁
*predict: 海娃
!! match !!
predict-target: (10, 10)-(10, 10)
Rouge-L: 1.0

**************************************************
抗日小英雄王朴送鸡毛信的抗日小英雄—[海娃]最年轻的抗日组织—抗日儿童团抗日小英雄—王二小银幕上的抗日小英雄—张嘎小说里的抗日小英雄—雨来
*question: 鸡毛信的小英雄是谁
*predict: 海娃
!! match !!
predict-target: (11, 11)-(11, 11)
Rouge-L: 1.0

**************************************************
3、[海娃]：电影《鸡毛信》主人公<e>4、雨来：语文课本《小英雄雨来》主人公
*question: 

...


**************************************************
1712年托马斯·纽科门和1769年[詹姆斯·瓦特]制造了早期的工业蒸汽机,他们对蒸汽机的发展都做出了自己的贡献.1807年罗伯特·富尔顿第一个成功地用蒸汽机来驱动轮船.<e>瓦特并不是蒸汽机的发明者,在他之前,早就出现了蒸汽机,即纽科门蒸汽机,但它的耗煤量大、效率低.
*question: 谁发明蒸汽机
*predict: 詹姆斯·瓦特制造了早期的工业蒸汽机,他们对蒸汽机的发展都做出了自己的贡献.1807年罗伯特·富尔顿
-- abs --: 0.023108240216970444
predict-target: (8, 34)-(8, 10)
Rouge-L: 0.1453488372091524

**************************************************
1764年,英国的仪器修理工[詹姆斯·瓦特]为格拉斯哥大学修理纽可门蒸汽机模型时,注意到了这一缺点,并于1765年发明了设有与汽缸壁分开的凝汽器的蒸汽机,并于1769年取得了英国的专利.
*question: 谁发明蒸汽机
*predict: 詹姆斯·瓦特为格拉斯哥大学修理纽可门蒸汽机
-- abs --: 0.020354514941573143
predict-target: (7, 15)-(7, 9)
Rouge-L: 0.3571428571424668

**************************************************
世界上第一台蒸汽机是由古希腊数学家亚历山大港的希罗（heroofalexandria）于1世纪发明的汽转球（aeolipile）,不过它只不过是一个玩具而已.约1679年法国物理学家丹尼斯·巴本在观察蒸汽逃离他的高压锅后制造了第一台蒸汽机的工作模型.约与此同时萨缪尔·莫兰也提出了蒸汽机的主意.1698年托马斯·塞维利、1712年托马斯·纽科门和1769年[詹姆斯·瓦特]制造了早期的工业蒸汽机,他们对蒸汽机的发展都做出了自己的贡献.
*question: 谁发明蒸汽机
*predict: 亚历山大港
-- abs --: 13.833943367004395
predict-target: (8, 8


**************************************************
作者:[高永]<e>制作·发行<e>出品年份----<e>官方网站-<e>发行卷册12<e>故事简介<e>《星座刑事》是高永倾注十年心血完成的一部作品，这部青春玄思漫画在占星术、刑侦、国际金融犯罪、魔法、毒品走私等诸种引人入胜的要素中跌宕起伏，荡气回肠。
*question: 星座刑事，梵天变的作者是：
*predict: 高永
!! match !!
predict-target: (2, 2)-(2, 2)
Rouge-L: 1.0

**************************************************
《星座刑事》是台湾漫画家[高永]的代表作。其中有很多塔罗牌的占卜情节，喜欢玩塔罗牌的朋友可以读读这套漫画。《星座刑事》的主角霍夫林，是国际刑警“海克里斯”组织成员之一，他的好搭档官明彦是中国香港人。喜欢喝热巧克力奶，非常可爱帅气。霍夫林性格比较成熟，心思比较缜密。<e>他们解决的案子都是与狮子心王有关，而狮子心王查理既是霍夫林最爱的老师，也是霍夫林的亲叔叔，海克里斯的雇主便是霍夫林的亲生父亲。但霍夫林并不知道。<e>《星座刑事》中讲述了霍夫林的父亲母亲和叔叔那一代的恩怨，这份恩怨一直到霍夫林长大之后。<e>有兴趣的朋友一定不能错过！！<e>《星座刑事》<e>作者:高永
*question: 星座刑事，梵天变的作者是：
*predict: 高永
!! match !!
predict-target: (7, 7)-(7, 7)
Rouge-L: 1.0

**************************************************
答：二十九、[高永]:代表作《星座刑事》、《梵天变》,台湾漫画界的帅哥,作品以优美...掉烧了(55555555),事后到书店去问又被告知没有了,所以到现在都不知道作者是谁...
*question: 星座刑事，梵天变的作者是：
*predict: 高永
!! match !!
predict-target: (4, 4)-(4, 4)
Rouge-L: 1.0

**************************************************
同时将其拉到自


**************************************************
王诩，又名王禅，[鬼谷子]，是历史上极富神秘色彩的传奇人物，春秋时人。常入云梦山采药修道。因隐居清溪之鬼谷，故自称鬼谷先生。春秋战国时期著名的思想家、谋略家，兵家、教育家，是纵横家的鼻祖，是中国历史上一位极具神秘色彩的人物，被誉为千古奇人，长于持身养性，精于心理揣摩，深明刚柔之势，通晓纵横捭阖之术，独具通天之智。他的弟子有兵家：孙膑、庞涓；纵横家：苏秦、张仪。
*question: 孙膑师承何人
*predict: 鬼谷子
!! match !!
predict-target: (5, 5)-(5, 5)
Rouge-L: 1.0

**************************************************
孙膑与庞涓均是[鬼谷子]的徒弟，后来庞涓担心孙膑的贤能，设法对他施以黥刑（脸上刺字）且挖掉膝盖骨。
*question: 孙膑是谁徒弟
*predict: 鬼谷子
!! match !!
predict-target: (6, 6)-(6, 6)
Rouge-L: 1.0

**************************************************
而野史中也有把孙膑与庞涓也归为其弟子之说（见《孙庞演义》）。相传其著有《[鬼谷子]》一书，始见着录于《隋书·经籍志》。原著散佚，今本《鬼谷子》三卷不全，而且怀疑是伪托所作。<e>鬼谷子先师孙滨、庞涓显赫一时的人物，俱拜在鬼谷子门下，世称鬼谷子先生。相传他曾随太上老君学习道学。而他自己亦著有不少关于行军兵法、道术、占卜、相人相宅。甚至为一个国事相其形气而知其兴亡盛衰。随他学艺的弟子苏秦张仪就随他学纵横之术，结果苏秦为六国大封相，而张仪更用远父近攻的方法，使泰国能统一天下。至于孙子的兵法，也学自鬼谷子，后世皆称孙子兵法，所有兵法，无出其右，其实他亦是鬼谷子先师的其中一位门生。<e>鬼谷子先师，有如此超人的本领，道家说他是上天一位神祗。法力高强，因当时世局混乱。所以上天派他下凡，传授兵法道法，奇辩之学，以创造奇才。鬼谷子先师，为诸子百家中的纵横家的始祖，亦为道家的诸位先师之一。后世流传有不少鬼谷子兵法、道法、奇门遁甲等学，博大精深，非深研，不能窥其奇奥。<e>鬼谷子先师


**************************************************
都属于广东[银汉]有限公司出品的时空猎人【街机格斗】
*question: 时空猎人的公司是哪个
*predict: 银汉有限公司
-- abs --: 1.0533068180084229
predict-target: (3, 4)-(3, 3)
Rouge-L: 0.5555555555549629

**************************************************
时空猎人是[银汉]公司代理的2d大型手机网络格斗游戏。
*question: 时空猎人的公司是哪个
*predict: 银汉
!! match !!
predict-target: (3, 3)-(3, 3)
Rouge-L: 1.0

**************************************************
图中一个是熊，有横霸无忌的样子，占东三省地方，是譬喻沙皇俄国；一个是斗牛犬，有守住不放的样子，占长江一带地方，是譬喻[英国]；一个是肠，有贪得无厌的样子，占山东地方，是譬喻德国；一个是青蛙，有任意收揽的样子，占广东、广西、云南地方，是譬喻法国；一个是太阳，他的光线到福建地方，是譬喻日本；一个是鹰，飞来分食，是譬喻美国。其旁题词曰：“沉沉酣睡我中华，那知爱国即爱家！国民知醒宜今醒，莫待土分裂似瓜。”《时局图》，除揭露帝国主义对中国的侵略，用虎、熊、蛙、太阳、鹰分别代表英、俄、法、日、美帝国主义国家外，还有揭露清政府腐败的内容：图上代表清政府的三个人物，一个手举铜钱，他是搜刮民财的贪官；一个不顾民族安危，正寻欢作乐；还有一个昏昏似睡者，手中拉着网绳，网中一人正念着“之乎者也”，另一人在马旁练武，揭示清政府用科举考试等升官之途愚弄人民。
*question: 时局图里虎代表什么
*predict: 鹰
-- abs --: 0.6128115653991699
predict-target: (95, 95)-(37, 37)
Rouge-L: 0.0

**************************************************
图中熊代表沙皇俄国,虎代表[英国],肠代表德国,青蛙代表法国,鹰代表美国,太阳

KeyboardInterrupt: 